# Machine Translation using OpenNMT

# Jamo and bpe Tokenization

In [1]:
cd /home/ubuntu/MT

/home/ubuntu/MT


In [2]:
!python OpenNMT-py/tools/learn_bpe.py -i OpenNMT-py/Data/tgt-train.txt -o OpenNMT-py/Data/tgt.code -s -1

In [ ]:
!python OpenNMT-py/tools/apply_jamo.py -i OpenNMT-py/Data/src-train.txt -o OpenNMT-py/Data/src-train-jamo.txt
!python OpenNMT-py/tools/apply_jamo.py -i OpenNMT-py/Data/src-valid.txt -o OpenNMT-py/Data/src-val-jamo.txt
!python OpenNMT-py/tools/apply_jamo.py -i OpenNMT-py/Data/src-test.txt -o OpenNMT-py/Data/src-test-jamo.txt

In [3]:
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/tgt.code -i OpenNMT-py/Data/tgt-train.txt -o OpenNMT-py/Data/tgt-train-bpe.txt
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/tgt.code -i OpenNMT-py/Data/tgt-valid.txt -o OpenNMT-py/Data/tgt-val-bpe.txt
!python OpenNMT-py/tools/apply_bpe.py -c OpenNMT-py/Data/tgt.code -i OpenNMT-py/Data/tgt-test.txt -o OpenNMT-py/Data/tgt-test-bpe.txt

# **Preprocess the data**

We will be working with some example data in data/ folder.

The data consists of parallel source (src) and target (tgt) data containing one sentence per line with tokens separated by a space:

1. src-train.txt

2. tgt-train.txt

3. src-val.txt

4. tgt-val.txt


Train data and validataion data are required for machine translation training.

Validation files are required and used to evaluate the convergence of the training. It usually contains no more than 5000 sentences.


> If you think about it briefly, you can specify the path of train data and validation data, and specify the path and name to save in -save_data.

> If you want to set vocab size add below command
<br>
-src_vocab_size 32000 -tgt_vocab_size 32000

The vocab size is usually 32000.

In [4]:
!python OpenNMT-py/preprocess.py -train_src OpenNMT-py/Data/src-train-jamo.txt -train_tgt OpenNMT-py/Data/tgt-train-bpe.txt -valid_src OpenNMT-py/Data/src-val-jamo.txt -valid_tgt OpenNMT-py/Data/tgt-val-bpe.txt -save_data OpenNMT-py/Data/jamo2bpe/demo -src_vocab_size -1 -tgt_vocab_size -1 -overwrite

[2020-12-07 13:22:05,242 INFO] Extracting features...
[2020-12-07 13:22:05,244 INFO]  * number of source features: 0.
[2020-12-07 13:22:05,244 INFO]  * number of target features: 0.
[2020-12-07 13:22:05,244 INFO] Building `Fields` object...
[2020-12-07 13:22:05,244 INFO] Building & saving training data...
[2020-12-07 13:22:24,753 INFO] Building shard 0.
[2020-12-07 13:24:26,623 INFO]  * saving 0th train data shard to OpenNMT-py/Data/jamo2bpe/demo.train.0.pt.
[2020-12-07 13:24:27,636 INFO]  * tgt vocab size: 139.
[2020-12-07 13:24:27,636 INFO]  * src vocab size: 91.
[2020-12-07 13:24:27,640 INFO] Building & saving validation data...
[2020-12-07 13:24:27,749 INFO] Building shard 0.
[2020-12-07 13:24:28,281 INFO]  * saving 0th valid data shard to OpenNMT-py/Data/jamo2bpe/demo.valid.0.pt.


!python OpenNMT-py/preprocess.py -train_src OpenNMT-py/Data/src-train-bpe.txt -train_tgt OpenNMT-py/Data/tgt-train-bpe.txt -valid_src OpenNMT-py/Data/src-val-bpe.txt -valid_tgt OpenNMT-py/Data/tgt-val-bpe.txt -save_data OpenNMT-py/Data/demo -src_vocab_size 32000 -tgt_vocab_size 32000

# **Train the data(Transformer)**

https://papers.nips.cc/paper/7181-attention-is-all-you-need.pdf


> If you get GPU-related errors, try halving batch_size

**Below is the full command, and if you want to know more about it, search about Transformer.**

!python OpenNMT-py/train.py -data OpenNMT-py/data/demo -save_model OpenNMT-py/data/model/model -layers 6 -rnn_size 512 -word_vec_size 512 -transformer_ff 2048 -heads 8 -encoder_type transformer -decoder_type transformer -position_encoding -train_steps 200000 -max_generator_batches 2 -dropout 0.1 -batch_size 4096 -batch_type tokens -normalization tokens -accum_count 2 -optim adam -adam_beta2 0.998 -decay_method noam -warmup_steps 8000 -learning_rate 2 -max_grad_norm 0 -param_init 0 -param_init_glorot -label_smoothing 0.1 -valid_steps 1000 -save_checkpoint_steps 1000 -world_size 1 -gpu_rank 0  

In [5]:
!nvidia-smi

Mon Dec  7 13:24:44 2020       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 440.64       Driver Version: 440.64       CUDA Version: 10.2     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  Quadro RTX 6000     On   | 00000000:00:06.0 Off |                    0 |
| N/A   26C    P8    16W / 250W |      0MiB / 22698MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
                                                                               
+-----------------------------------------------------------------------------+
| Processes:                                                       GPU Memory |
|  GPU  

In [6]:
!python OpenNMT-py/train.py -data OpenNMT-py/Data/jamo2bpe/demo -save_model OpenNMT-py/Data/jamo2bpe/model/model -layers 6 -rnn_size 512 -word_vec_size 512 -transformer_ff 2048 -heads 8 -encoder_type transformer -decoder_type transformer -position_encoding -train_steps 50000 -max_generator_batches 2 -dropout 0.1 -batch_size 4096 -batch_type tokens -normalization tokens -accum_count 2 -optim adam -adam_beta2 0.998 -decay_method noam -warmup_steps 8000 -learning_rate 2 -max_grad_norm 0 -param_init 0 -param_init_glorot -label_smoothing 0.1 -valid_steps 1000 -save_checkpoint_steps 100 -world_size 1 -gpu_rank 0 -tensorboard -tensorboard_log_dir 'logs/my_board/jamo2bpe'

[2020-12-07 13:25:42,565 INFO]  * src vocab size = 91
[2020-12-07 13:25:42,565 INFO]  * tgt vocab size = 139
[2020-12-07 13:25:42,565 INFO] Building model...
[2020-12-07 13:25:49,243 INFO] NMTModel(
  (encoder): TransformerEncoder(
    (embeddings): Embeddings(
      (make_embedding): Sequential(
        (emb_luts): Elementwise(
          (0): Embedding(91, 512, padding_idx=1)
        )
        (pe): PositionalEncoding(
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (transformer): ModuleList(
      (0): TransformerEncoderLayer(
        (self_attn): MultiHeadedAttention(
          (linear_keys): Linear(in_features=512, out_features=512, bias=True)
          (linear_values): Linear(in_features=512, out_features=512, bias=True)
          (linear_query): Linear(in_features=512, out_features=512, bias=True)
          (softmax): Softmax(dim=-1)
          (dropout): Dropout(p=0.1, inplace=False)
          (final_linear): Linear(in_features=512, out_features=512

          (dropout): Dropout(p=0.1, inplace=False)
          (final_linear): Linear(in_features=512, out_features=512, bias=True)
        )
        (feed_forward): PositionwiseFeedForward(
          (w_1): Linear(in_features=512, out_features=2048, bias=True)
          (w_2): Linear(in_features=2048, out_features=512, bias=True)
          (layer_norm): LayerNorm((512,), eps=1e-06, elementwise_affine=True)
          (dropout_1): Dropout(p=0.1, inplace=False)
          (relu): ReLU()
          (dropout_2): Dropout(p=0.1, inplace=False)
        )
        (layer_norm_1): LayerNorm((512,), eps=1e-06, elementwise_affine=True)
        (layer_norm_2): LayerNorm((512,), eps=1e-06, elementwise_affine=True)
        (drop): Dropout(p=0.1, inplace=False)
      )
    )
    (layer_norm): LayerNorm((512,), eps=1e-06, elementwise_affine=True)
  )
  (generator): Sequential(
    (0): Linear(in_features=512, out_features=139, bias=True)
    (1): Cast()
    (2): LogSoftmax(dim=-1)
  )
)
[2020-12-07 13:25:4

[2020-12-07 13:30:02,237 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 13:30:02,391 INFO] number of examples: 3234
[2020-12-07 13:30:09,709 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 13:30:09,856 INFO] number of examples: 3234
[2020-12-07 13:30:17,573 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 13:30:17,737 INFO] number of examples: 3234
[2020-12-07 13:30:18,881 INFO] Step 700/50000; acc:  37.50; ppl:  6.52; xent: 1.87; lr: 0.00009; 19749/17309 tok/s;    269 sec
[2020-12-07 13:30:18,886 INFO] Saving checkpoint OpenNMT-py/Data/jamo2bpe/model/model_step_700.pt
[2020-12-07 13:30:26,636 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 13:30:26,787 INFO] number of examples: 3234
[2020-12-07 13:30:34,436 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 13:30:34,589 INFO] number of examples: 3234
[2020-12-07 13:30:38,944 INFO]

[2020-12-07 13:35:29,693 INFO] number of examples: 3234
[2020-12-07 13:35:31,975 INFO] Step 1400/50000; acc:  64.76; ppl:  2.83; xent: 1.04; lr: 0.00017; 19228/16737 tok/s;    583 sec
[2020-12-07 13:35:31,981 INFO] Saving checkpoint OpenNMT-py/Data/jamo2bpe/model/model_step_1400.pt
[2020-12-07 13:35:39,218 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 13:35:39,367 INFO] number of examples: 3234
[2020-12-07 13:35:47,204 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 13:35:47,464 INFO] number of examples: 3234
[2020-12-07 13:35:52,944 INFO] Step 1450/50000; acc:  67.19; ppl:  2.65; xent: 0.97; lr: 0.00018; 17569/15259 tok/s;    604 sec
[2020-12-07 13:35:54,821 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 13:35:54,972 INFO] number of examples: 3234
[2020-12-07 13:36:02,693 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 13:36:02,847 INFO] number of examples

[2020-12-07 13:40:53,145 INFO] number of examples: 3234
[2020-12-07 13:41:00,827 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 13:41:00,980 INFO] number of examples: 3234
[2020-12-07 13:41:07,672 INFO] Step 2150/50000; acc:  92.00; ppl:  1.41; xent: 0.34; lr: 0.00027; 17961/15684 tok/s;    918 sec
[2020-12-07 13:41:08,471 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 13:41:08,628 INFO] number of examples: 3234
[2020-12-07 13:41:16,330 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 13:41:16,597 INFO] number of examples: 3234
[2020-12-07 13:41:24,075 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 13:41:24,228 INFO] number of examples: 3234
[2020-12-07 13:41:26,852 INFO] Step 2200/50000; acc:  92.91; ppl:  1.38; xent: 0.32; lr: 0.00027; 19410/16913 tok/s;    937 sec
[2020-12-07 13:41:26,857 INFO] Saving checkpoint OpenNMT-py/Data/jamo2bpe/model/model_step_2

...

[2020-12-07 19:02:34,257 INFO] number of examples: 3234
[2020-12-07 19:02:42,126 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:02:42,288 INFO] number of examples: 3234
[2020-12-07 19:02:42,691 INFO] Step 46700/50000; acc:  99.96; ppl:  1.00; xent: 0.00; lr: 0.00041; 19401/16867 tok/s;  20213 sec
[2020-12-07 19:02:42,696 INFO] Saving checkpoint OpenNMT-py/Data/jamo2bpe/model/model_step_46700.pt
[2020-12-07 19:02:54,999 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:02:55,394 INFO] number of examples: 3234
[2020-12-07 19:03:03,285 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:03:03,448 INFO] number of examples: 3234
[2020-12-07 19:03:07,156 INFO] Step 46750/50000; acc:  99.96; ppl:  1.00; xent: 0.00; lr: 0.00041; 15052/13182 tok/s;  20238 sec
[2020-12-07 19:03:10,961 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:03:11,119 INFO] number of examp

[2020-12-07 19:08:07,776 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:08:07,932 INFO] number of examples: 3234
[2020-12-07 19:08:15,684 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:08:15,848 INFO] number of examples: 3234
[2020-12-07 19:08:20,699 INFO] Step 47450/50000; acc:  99.97; ppl:  1.00; xent: 0.00; lr: 0.00041; 17874/15565 tok/s;  20551 sec
[2020-12-07 19:08:23,338 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:08:23,615 INFO] number of examples: 3234
[2020-12-07 19:08:31,348 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:08:31,509 INFO] number of examples: 3234
[2020-12-07 19:08:39,018 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:08:39,184 INFO] number of examples: 3234
[2020-12-07 19:08:39,966 INFO] Step 47500/50000; acc:  99.96; ppl:  1.00; xent: 0.00; lr: 0.00041; 19352/16859 tok/s;  20571 s

[2020-12-07 19:13:37,620 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:13:37,778 INFO] number of examples: 3234
[2020-12-07 19:13:45,491 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:13:45,767 INFO] number of examples: 3234
[2020-12-07 19:13:53,142 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:13:53,299 INFO] number of examples: 3234
[2020-12-07 19:13:55,168 INFO] Step 48200/50000; acc:  99.96; ppl:  1.00; xent: 0.00; lr: 0.00040; 19576/17093 tok/s;  20886 sec
[2020-12-07 19:13:55,173 INFO] Saving checkpoint OpenNMT-py/Data/jamo2bpe/model/model_step_48200.pt
[2020-12-07 19:14:02,616 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:14:02,776 INFO] number of examples: 3234
[2020-12-07 19:14:10,260 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:14:10,418 INFO] number of examples: 3234
[2020-12-07 19:14:15,580 I

[2020-12-07 19:18:39,832 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:18:39,992 INFO] number of examples: 3234
[2020-12-07 19:18:47,498 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:18:47,654 INFO] number of examples: 3234
[2020-12-07 19:18:53,991 INFO] Step 48950/50000; acc:  99.96; ppl:  1.00; xent: 0.00; lr: 0.00040; 17397/15129 tok/s;  21185 sec
[2020-12-07 19:18:55,461 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:18:55,741 INFO] number of examples: 3234
[2020-12-07 19:19:03,105 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:19:03,262 INFO] number of examples: 3234
[2020-12-07 19:19:11,014 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:19:11,171 INFO] number of examples: 3234
[2020-12-07 19:19:13,099 INFO] Step 49000/50000; acc:  99.97; ppl:  1.00; xent: 0.00; lr: 0.00040; 19485/16987 tok/s;  21204 s

[2020-12-07 19:24:09,543 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:24:09,702 INFO] number of examples: 3234
[2020-12-07 19:24:17,091 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:24:17,247 INFO] number of examples: 3234
[2020-12-07 19:24:24,958 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:24:25,242 INFO] number of examples: 3234
[2020-12-07 19:24:28,242 INFO] Step 49700/50000; acc:  99.97; ppl:  1.00; xent: 0.00; lr: 0.00040; 19524/17066 tok/s;  21519 sec
[2020-12-07 19:24:28,247 INFO] Saving checkpoint OpenNMT-py/Data/jamo2bpe/model/model_step_49700.pt
[2020-12-07 19:24:34,321 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:24:34,477 INFO] number of examples: 3234
[2020-12-07 19:24:42,149 INFO] Loading dataset from OpenNMT-py/Data/jamo2bpe/demo.train.0.pt
[2020-12-07 19:24:42,306 INFO] number of examples: 3234
[2020-12-07 19:24:48,549 I

# **Translate**

Now that you have your model, you can start translating.

-model ==> Setting your model

Output predictions into pred.txt

In [17]:
!python OpenNMT-py/translate.py -model OpenNMT-py/Data/jamo2bpe/model/model_step_50000.pt -src OpenNMT-py/Data/src-test-jamo.txt -output OpenNMT-py/Data/jamo2bpe/pred_50k.txt -replace_unk -verbose -beam_size 1 -gpu 0

[2020-12-11 16:06:05,326 INFO] Translating shard 0.
[2020-12-11 16:06:06,271 INFO] 
SENT 1: ['"', 'ㄱ', 'ㅕ', 'ㅇ', 'ㅊ', 'ㅏ', 'ㄹ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅅ', 'ㅓ', 'ㄹ', 'ㅁ', 'ㅕ', 'ㅇ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅂ', 'ㅗ', 'ㅁ', 'ㅕ', 'ㄴ', ',', 'ᴥ', 'ㅅ', 'ㅗ', 'ㄴ', 'ㄴ', 'ㅣ', 'ㅁ', 'ㅇ', 'ㅡ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㅍ', 'ㅣ', 'ㅅ', 'ㅣ', 'ㅂ', 'ㅏ', 'ㅇ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅊ', 'ㅏ', 'ㅈ', 'ㅇ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㄱ', 'ㅣ', 'ㅁ', 'ㅆ', 'ㅣ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㄷ', 'ㅏ', 'ㄹ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅗ', 'ㄴ', 'ㄴ', 'ㅣ', 'ㅁ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㄴ', 'ㅏ', 'ㅁ', 'ㄱ', 'ㅣ', 'ㄴ', 'ᴥ', 'ㅇ', 'ㅡ', 'ㅁ', 'ㅅ', 'ㅣ', 'ㄱ', 'ㅁ', 'ㅜ', 'ㄹ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅈ', 'ㅏ', 'ㄹ', 'ㅣ', 'ㅇ', 'ㅔ', 'ㅅ', 'ㅓ', 'ᴥ', 'ㅊ', 'ㅣ', 'ㅇ', 'ㅝ', 'ㄷ', 'ㅏ', 'ㄹ', 'ㄹ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅇ', 'ㅛ', 'ㄱ', 'ㅜ', 'ㄹ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㄷ', 'ㅏ', 'ᴥ', 'ㅅ', 'ㅣ', 'ㄴ', 'ㅆ', 'ㅣ', 'ㅇ', 'ㅘ', 'ᴥ', 'ㅁ', 'ㅏ', 'ㄹ', 'ㄷ', 'ㅏ', 'ㅌ', 'ㅜ', 'ㅁ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅎ', 'ㅐ', 'ㅆ', 'ㄷ', 'ㅏ', 'ㄱ', 'ㅗ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㄴ', 'ㄷ', 'ㅏ', '.', '"']
PRED 1: "@@ A@@ f@@ t@@ e@@ r@@ w@@ a@@ r@@ d@@ , a f@@ o

[2020-12-11 16:06:07,085 INFO] 
SENT 31: ['"', 'ㄷ', 'ㅏ', 'ㄴ', 'ㄷ', 'ㅗ', 'ㄱ', 'ᴥ', 'ㅋ', 'ㅗ', 'ㄴ', 'ㅅ', 'ㅓ', 'ㅌ', 'ㅡ', 'ᴥ', 'ㅁ', 'ㅜ', 'ㄷ', 'ㅐ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅇ', 'ㅏ', 'ㄴ', 'ㅣ', 'ㄴ', ',', 'ᴥ', 'ㅈ', 'ㅜ', 'ᴥ', 'ㅅ', 'ㅣ', 'ㅊ', 'ㅓ', 'ㅇ', 'ㅊ', 'ㅡ', 'ㅇ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㅊ', 'ㅓ', 'ㅇ', 'ㅅ', 'ㅗ', 'ㄴ', 'ㅕ', 'ㄴ', 'ㄷ', 'ㅡ', 'ㄹ', 'ㅇ', 'ㅣ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅣ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅅ', 'ㅣ', 'ㄱ', 'ᴥ', 'ㅁ', 'ㅜ', 'ㄷ', 'ㅐ', 'ㅇ', 'ㅕ', 'ㅆ', 'ㄷ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅈ', 'ㅓ', 'ㅁ', 'ㅇ', 'ㅔ', 'ㅅ', 'ㅓ', 'ᴥ', 'ㅎ', 'ㅘ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅇ', 'ㅢ', 'ㅅ', 'ㅏ', 'ㅇ', 'ᴥ', 'ㅅ', 'ㅓ', 'ㄴ', 'ㅌ', 'ㅐ', 'ㄱ', 'ㅇ', 'ㅔ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅇ', 'ㅏ', 'ㅅ', 'ㅟ', 'ㅇ', 'ㅜ', 'ㅁ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㄴ', 'ㅏ', 'ㅁ', 'ㄴ', 'ㅡ', 'ㄴ', 'ㄷ', 'ㅏ', '.', '"']
PRED 31: "@@ T@@ h@@ e b@@ a@@ l@@ l f@@ a@@ r@@ m@@ e@@ , t@@ h@@ e b@@ e@@ s@@ t p@@ o@@ i@@ n@@ t i@@ s b@@ e@@ h@@ i@@ n@@ d i@@ n t@@ h@@ e t@@ w@@ o c@@ o@@ u@@ t@@ s@@ .@@ "
PRED SCORE: -0.0785

[2020-12-11 16:06:07,085 INFO] 
SENT 32: ['"', 'ㅊ', 'ㅜ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅊ', 'ㅟ', 'ㅇ',

[2020-12-11 16:06:07,796 INFO] 
SENT 61: ['ㅇ', 'ㅣ', 'ㅇ', 'ㅘ', 'ᴥ', 'ㄷ', 'ㅏ', 'ㄹ', 'ㄹ', 'ㅣ', 'ᴥ', 'ㅇ', 'ㅜ', 'ㄱ', 'ㅣ', 'ㅇ', 'ㅔ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅁ', 'ㅗ', 'ㄱ', 'ㅊ', 'ㅗ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅁ', 'ㅜ', 'ㅅ', 'ㅓ', 'ㅇ', 'ㅎ', 'ㅐ', 'ᴥ', 'ㄱ', 'ㅜ', 'ㅊ', 'ㅜ', 'ㅇ', 'ㅈ', 'ㅔ', 'ㅇ', 'ㅘ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㅇ', 'ㅅ', 'ㅐ', 'ㅇ', 'ㅈ', 'ㅔ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅅ', 'ㅜ', 'ㅇ', 'ㅛ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㄴ', 'ㅗ', 'ㅍ', 'ㄷ', 'ㅏ', '.']
PRED 61: S@@ o@@ l@@ u@@ t@@ i@@ c@@ i@@ e@@ s a@@ r@@ e m@@ a@@ t@@ c@@ h@@ e@@ r i@@ n@@ t@@ e@@ r@@ e@@ s@@ t i@@ n t@@ h@@ e f@@ i@@ r@@ s@@ t i@@ s t@@ o@@ o f@@ a@@ l@@ .
PRED SCORE: -0.0779

[2020-12-11 16:06:07,796 INFO] 
SENT 62: ['ㄷ', 'ㅐ', 'ㅈ', 'ㅓ', 'ㄴ', 'ㅈ', 'ㅣ', 'ㅇ', 'ㅕ', 'ㄱ', 'ᴥ', 'ㄱ', 'ㅕ', 'ㅇ', 'ㅈ', 'ㅔ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅎ', 'ㅡ', 'ㄴ', 'ㄷ', 'ㅡ', 'ㄹ', 'ㄹ', 'ㅣ', 'ㄱ', 'ㅗ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㅆ', 'ㄷ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅌ', 'ㅗ', 'ㅇ', 'ㄱ', 'ㅖ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅈ', 'ㅣ', 'ㄴ', 'ㅏ', 'ㄴ', 'ㅎ', 'ㅐ', 'ㅂ', 'ㅜ', 'ㅌ', 'ㅓ', 'ᴥ', 'ㅇ', 'ㅕ', 'ㄴ', 'ㅇ', 'ㅣ', 'ㅇ', 'ㅓ', 'ᴥ', 'ㄴ', 'ㅏ', 'ㅇ', 'ㅗ', 'ㄱ', 'ㅗ'

[2020-12-11 16:06:08,552 INFO] 
SENT 91: ['"', 'ㅅ', 'ㅗ', 'ㄴ', 'ㅅ', 'ㅓ', 'ㄱ', 'ㅎ', 'ㅢ', 'ᴥ', 'j', 't', 'b', 'c', 'ᴥ', 'ㄷ', 'ㅐ', 'ㅍ', 'ㅛ', 'ㅇ', 'ㅣ', 'ㅅ', 'ㅏ', 'ㄹ', 'ㅗ', 'ㅂ', 'ㅜ', 'ㅌ', 'ㅓ', 'ᴥ', 'ㅍ', 'ㅗ', 'ㄱ', 'ㅎ', 'ㅐ', 'ㅇ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㄷ', 'ㅏ', 'ㅇ', 'ㅎ', 'ㅐ', 'ㅆ', 'ㄷ', 'ㅏ', 'ㄱ', 'ㅗ', 'ᴥ', 'ㅈ', 'ㅜ', 'ㅈ', 'ㅏ', 'ㅇ', 'ㅎ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅍ', 'ㅡ', 'ㄹ', 'ㅣ', 'ㄹ', 'ㅐ', 'ㄴ', 'ㅅ', 'ㅓ', 'ᴥ', 'ㄱ', 'ㅣ', 'ㅈ', 'ㅏ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅅ', 'ㅗ', 'ㄴ', 'ᴥ', 'ㄷ', 'ㅐ', 'ㅍ', 'ㅛ', 'ㄹ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅎ', 'ㅕ', 'ㅂ', 'ㅂ', 'ㅏ', 'ㄱ', ',', 'ᴥ', 'ㅁ', 'ㅕ', 'ㅇ', 'ㅇ', 'ㅖ', 'ㅎ', 'ㅞ', 'ㅅ', 'ㅗ', 'ㄴ', 'ᴥ', 'ㅎ', 'ㅕ', 'ㅁ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㄷ', 'ㅡ', 'ㅇ', 'ㅇ', 'ㅡ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㄱ', 'ㅓ', 'ㅁ', 'ㅊ', 'ㅏ', 'ㄹ', 'ㅇ', 'ㅔ', 'ᴥ', 'ㅊ', 'ㅜ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㄱ', 'ㅗ', 'ㅅ', 'ㅗ', 'ㅎ', 'ㅐ', 'ㅆ', 'ㄷ', 'ㅏ', '.', '"']
PRED 91: "@@ A@@ f@@ t@@ e@@ r t@@ h@@ e e@@ x@@ p@@ e@@ r@@ i@@ e@@ n@@ c@@ e H@@ o@@ -@@ m@@ n@@ e@@ d S@@ o@@ o@@ n p@@ u@@ b@@ l@@ i@@ c r@@ e@@ p@@ a@@ r@@ t@@ e@@ d@@ .@@ "
PRED SCORE: -0.0788

[2020-12-11 1

[2020-12-11 16:06:09,233 INFO] 
SENT 121: ['ㄱ', 'ㅡ', 'ᴥ', 'ㄱ', 'ㅘ', 'ㅈ', 'ㅓ', 'ㅇ', 'ㅇ', 'ㅔ', 'ㅅ', 'ㅓ', 'ᴥ', 'ㄱ', 'ㅏ', 'ㅈ', 'ㅏ', 'ㅇ', 'ᴥ', 'ㅈ', 'ㅜ', 'ㅇ', 'ㅅ', 'ㅣ', 'ㅎ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㄱ', 'ㅓ', 'ㅅ', 'ㅇ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅁ', 'ㅏ', 'ㄴ', 'ㅎ', 'ㅘ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅌ', 'ㅡ', 'ㄱ', 'ㅂ', 'ㅕ', 'ㄹ', 'ㅎ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㅇ', 'ㅖ', 'ㅅ', 'ㅜ', 'ㄹ', 'ㅅ', 'ㅓ', 'ㅇ', 'ㅇ', 'ㅔ', 'ᴥ', 'ㅁ', 'ㅏ', 'ㄴ', 'ㅎ', 'ㅘ', 'ㄱ', 'ㅏ', 'ㅃ', 'ㅜ', 'ㄴ', 'ᴥ', 'ㅇ', 'ㅏ', 'ㄴ', 'ㅣ', 'ㄹ', 'ㅏ', 'ᴥ', 'ㅁ', 'ㅗ', 'ㄷ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㄱ', 'ㅜ', 'ㄱ', 'ㅁ', 'ㅣ', 'ㄴ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㅁ', 'ㄲ', 'ㅔ', 'ᴥ', 'ㅊ', 'ㅏ', 'ㅁ', 'ㅇ', 'ㅕ', 'ㅎ', 'ㅏ', 'ㄹ', 'ᴥ', 'ㅅ', 'ㅜ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㅆ', 'ㄷ', 'ㅗ', 'ㄹ', 'ㅗ', 'ㄱ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㄱ', 'ㅓ', 'ㅅ', 'ㅇ', 'ㅣ', 'ㄷ', 'ㅏ', '.']
PRED 121: I t@@ h@@ i@@ n@@ k a@@ l@@ l p@@ l@@ a@@ y@@ e@@ r s@@ i@@ v@@ e s@@ t@@ o@@ r@@ y m@@ y d@@ i@@ s@@ p@@ e@@ r@@ a@@ t@@ e@@ d i@@ n t@@ h@@ e g@@ a@@ m@@ e@@ .
PRED SCORE: -0.0770

[2020-12-11 16:06:09,234 INFO] 
SENT 122: ['"', 'ㅂ', 'ㅜ', 'ㅅ', '

...

[2020-12-11 16:08:59,358 INFO] 
SENT 7891: ['ㄱ', 'ㅡ', 'ㅈ', 'ㅜ', 'ㅇ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㄴ', 'ㅏ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㄷ', 'ㅗ', 'ㅅ', 'ㅣ', 'ㄱ', 'ㅖ', 'ㅎ', 'ㅚ', 'ㄱ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅌ', 'ㅗ', 'ㅇ', 'ㅎ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㄱ', 'ㅗ', 'ㅇ', 'ㄷ', 'ㅗ', 'ㅇ', 'ㅊ', 'ㅔ', 'ᴥ', 'ㅈ', 'ㅗ', 'ㅅ', 'ㅓ', 'ㅇ', 'ㄱ', 'ㅘ', 'ᴥ', 'ㄱ', 'ㅗ', 'ㅇ', 'ㅇ', 'ㅠ', 'ㄱ', 'ㅏ', 'ㅊ', 'ㅣ', 'ᴥ', 'ㅅ', 'ㅣ', 'ㄹ', 'ㅎ', 'ㅕ', 'ㄴ', 'ㅇ', 'ㅣ', 'ㄷ', 'ㅏ', '.']
PRED 7891: T@@ h@@ e w@@ i@@ l@@ l b@@ e s@@ e@@ r@@ v@@ e@@ s a@@ r@@ e t@@ h@@ e r@@ e@@ m@@ a@@ i@@ n@@ s a@@ s t@@ h@@ e p@@ l@@ a@@ c@@ e@@ .
PRED SCORE: -0.0791

[2020-12-11 16:08:59,358 INFO] 
SENT 7892: ['ㅁ', 'ㅗ', 'ㄷ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅁ', 'ㅔ', 'ㅁ', 'ㅂ', 'ㅓ', 'ㄱ', 'ㅏ', 'ᴥ', '1', '0', 'ㄷ', 'ㅐ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㄱ', 'ㅜ', 'ㅅ', 'ㅓ', 'ㅇ', 'ㄷ', 'ㅚ', 'ㄴ', 'ᴥ', '6', 'ㅇ', 'ㅣ', 'ㄴ', 'ㅈ', 'ㅗ', 'ᴥ', 'ㄱ', 'ㅡ', 'ㄹ', 'ㅜ', 'ㅂ', 'ᴥ', 'ㄷ', 'ㅓ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㅅ', 'ㅡ', 'ㅌ', 'ㅡ', 'ᴥ', 'ㄹ', 'ㅏ', 'ㅇ', 'ㅣ', 'ㅌ', 'ㅡ', 'ᴥ', 'ㅍ', 'ㅗ', 'ㄱ', 'ㅎ', 'ㅐ', 'ㅇ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㄱ', 'ㅓ', 'ㄴ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅊ', 'ㅓ', 'ㄹ',

[2020-12-11 16:09:00,018 INFO] 
SENT 7921: ['ㄱ', 'ㅝ', 'ㄴ', 'ㅇ', 'ㅛ', 'ㅇ', 'ㅅ', 'ㅜ', 'ᴥ', 'ㅈ', 'ㅜ', 'ㅇ', 'ㅜ', 'ㅈ', 'ㅡ', 'ㅂ', 'ㅔ', 'ㅋ', 'ㅣ', 'ㅅ', 'ㅡ', 'ㅌ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㄷ', 'ㅐ', 'ㅅ', 'ㅏ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅡ', 'ㅁ', 'ㅏ', 'ㅌ', 'ㅡ', 'ㅁ', 'ㅣ', 'ㅌ', 'ㅓ', 'ᴥ', 'ㅍ', 'ㅡ', 'ㄹ', 'ㅗ', 'ㅈ', 'ㅔ', 'ㄱ', 'ㅌ', 'ㅡ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅅ', 'ㅓ', 'ㅇ', 'ㄱ', 'ㅗ', 'ㅇ', 'ᴥ', 'ㅊ', 'ㅜ', 'ㅈ', 'ㅣ', 'ㄴ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅂ', 'ㅏ', 'ㅌ', 'ㅏ', 'ㅇ', 'ㅇ', 'ㅡ', 'ㄹ', 'ㅗ', 'ᴥ', 'k', 't', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅇ', 'ㅜ', 'ㅈ', 'ㅡ', 'ㅂ', 'ㅔ', 'ㄱ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㄷ', 'ㅏ', 'ㅇ', 'ㅑ', 'ㅇ', 'ㅎ', 'ㅏ', 'ㄴ', 'ᴥ', 'i', 'c', 't', 'ᴥ', 'ㅂ', 'ㅜ', 'ㄴ', 'ㅇ', 'ㅑ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㅎ', 'ㅘ', 'ㄱ', 'ㄷ', 'ㅐ', 'ㄷ', 'ㅙ', 'ᴥ', 'ㄴ', 'ㅏ', 'ㄱ', 'ㅏ', 'ㄱ', 'ㅣ', 'ㄹ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅂ', 'ㅏ', 'ㄹ', 'ㅏ', 'ㄴ', 'ㄷ', 'ㅏ', 'ㄱ', 'ㅗ', 'ᴥ', 'ㅂ', 'ㅏ', 'ㄺ', 'ㅎ', 'ㅕ', 'ㅆ', 'ㄷ', 'ㅏ', '.']
PRED 7921: B@@ o@@ t@@ h a l@@ a@@ r@@ g@@ e@@ s@@ t p@@ r@@ o@@ f@@ e@@ c@@ t f@@ r@@ o@@ m S@@ u@@ t@@ h K@@ o@@ r@@ e@@ a h@@ a@@ s b@@ e@@ e@@ n i@

[2020-12-11 16:09:00,652 INFO] 
SENT 7951: ['ㅋ', 'ㅏ', 'ㅌ', 'ㅏ', 'ㄹ', 'ㅡ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', '4', 'ㄱ', 'ㅕ', 'ㅇ', 'ㄱ', 'ㅣ', 'ㅅ', 'ㅓ', 'ᴥ', '1', '0', 'ㄱ', 'ㅗ', 'ㄹ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅎ', 'ㅓ', 'ㅇ', 'ㅛ', 'ㅇ', 'ㅎ', 'ㅐ', 'ㅆ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅈ', 'ㅓ', 'ㅇ', 'ㄷ', 'ㅗ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㅅ', 'ㅜ', 'ㅂ', 'ㅣ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅇ', 'ㅑ', 'ㄱ', 'ㅎ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㅌ', 'ㅣ', 'ㅁ', 'ㅇ', 'ㅣ', 'ㄱ', 'ㅣ', 'ᴥ', 'ㄸ', 'ㅐ', 'ㅁ', 'ㅜ', 'ㄴ', 'ㅇ', 'ㅔ', 'ᴥ', 'ㅈ', 'ㅓ', 'ㅇ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅈ', 'ㅓ', 'ㄱ', 'ㅇ', 'ㅡ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㄷ', 'ㅐ', 'ㅎ', 'ㅏ', 'ㅁ', 'ㅕ', 'ㄴ', 'ᴥ', 'ㅊ', 'ㅜ', 'ㅇ', 'ㅂ', 'ㅜ', 'ㄴ', 'ㅎ', 'ㅣ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㄱ', 'ㅣ', 'ㄹ', 'ᴥ', 'ㅅ', 'ㅜ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㅆ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㄷ', 'ㅐ', 'ㄷ', 'ㅏ', '.']
PRED 7951: T@@ h@@ e b@@ i@@ g@@ g@@ e@@ s@@ t f@@ i@@ r@@ s@@ t t@@ a@@ k@@ e o@@ u@@ t t@@ h@@ e W@@ o@@ r@@ l@@ d a@@ t t@@ h@@ e 1@@ 0 p@@ l@@ a@@ y@@ e@@ r@@ .
PRED SCORE: -0.0771

[2020-12-11 16:09:00,652 INFO] 
SENT 7952: ['ㄷ', 'ㅐ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅇ', 'ㅔ', 'ㅅ', 'ㅓ', '

[2020-12-11 16:09:01,276 INFO] 
SENT 7981: ['"', 'ㄱ', 'ㅡ', 'ㄴ', 'ㄷ', 'ㅐ', 'ㄱ', 'ㅓ', 'ㄴ', 'ㅊ', 'ㅜ', 'ㄱ', 'ㅁ', 'ㅜ', 'ㄹ', 'ᴥ', 'ㄱ', 'ㅣ', 'ㄹ', 'ㅗ', 'ㄱ', 'ㅂ', 'ㅗ', 'ㅈ', 'ㅗ', 'ㄴ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㅇ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅈ', 'ㅣ', 'ㄴ', 'ㅏ', 'ㄴ', 'ᴥ', '2', '0', '1', '0', 'ㄴ', 'ㅕ', 'ㄴ', 'ㅂ', 'ㅜ', 'ㅌ', 'ㅓ', 'ᴥ', 'ㄱ', 'ㅘ', 'ㅇ', 'ㅈ', 'ㅜ', 'ㅅ', 'ㅣ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㅊ', 'ㅜ', 'ㅈ', 'ㅣ', 'ㄴ', 'ㅎ', 'ㅏ', 'ㄱ', 'ㅗ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㅆ', 'ㄴ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㅇ', 'ㅡ', 'ㄹ', 'ㅗ', ',', 'ᴥ', 'ㄱ', 'ㅡ', 'ㄷ', 'ㅗ', 'ㅇ', 'ㅇ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㄷ', 'ㅐ', 'ㅅ', 'ㅏ', 'ㅇ', 'ᴥ', 'ㄱ', 'ㅓ', 'ㄴ', 'ㅁ', 'ㅜ', 'ㄹ', 'ㅈ', 'ㅜ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㅂ', 'ㅣ', 'ㅎ', 'ㅕ', 'ㅂ', 'ㅈ', 'ㅗ', 'ㅇ', 'ㅘ', 'ᴥ', 'ㄱ', 'ㅓ', 'ㄴ', 'ㅊ', 'ㅜ', 'ㄱ', 'ㅁ', 'ㅜ', 'ㄹ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㄴ', 'ㅈ', 'ㅐ', 'ㄹ', 'ㅗ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㅊ', 'ㅜ', 'ㅈ', 'ㅣ', 'ㄴ', 'ㅇ', 'ㅔ', 'ᴥ', 'ㅈ', 'ㅓ', 'ㄱ', 'ㅈ', 'ㅣ', 'ᴥ', 'ㅇ', 'ㅏ', 'ㄶ', 'ㅇ', 'ㅡ', 'ㄴ', 'ᴥ', 'ㅇ', 'ㅓ', 'ㄹ', 'ㅕ', 'ㅇ', 'ㅜ', 'ㅁ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㄱ', 'ㅕ', 'ㄲ', 'ㅇ', '

[2020-12-11 16:09:01,741 INFO] 
SENT 8011: ['ㄷ', 'ㅏ', 'ㅁ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㅂ', 'ㅜ', 'ㄱ', 'ㅁ', 'ㅣ', 'ㄱ', 'ㅏ', 'ᴥ', 'ㄱ', 'ㅗ', 'ㅇ', 'ㄷ', 'ㅗ', 'ㅇ', 'ᴥ', 'ㅇ', 'ㅠ', 'ㅎ', 'ㅐ', 'ㅂ', 'ㅏ', 'ㄹ', 'ㄱ', 'ㅜ', 'ㄹ', 'ᴥ', 'ㅅ', 'ㅏ', 'ㅇ', 'ㅓ', 'ㅂ', 'ㅇ', 'ㅔ', 'ᴥ', 'ㅎ', 'ㅏ', 'ㅂ', 'ㅇ', 'ㅢ', 'ㅎ', 'ㅏ', 'ㄴ', 'ㄷ', 'ㅏ', 'ㅁ', 'ㅕ', 'ㄴ', 'ᴥ', 'ㅁ', 'ㅣ', 'ㄱ', 'ㅜ', 'ㄱ', 'ᴥ', 'ㅈ', 'ㅏ', 'ㅇ', 'ㅂ', 'ㅣ', 'ㅇ', 'ㅢ', 'ᴥ', 'ㄷ', 'ㅐ', 'ㅂ', 'ㅜ', 'ㄱ', 'ᴥ', 'ㅂ', 'ㅏ', 'ㄴ', 'ㅇ', 'ㅣ', 'ㅂ', 'ㄱ', 'ㅘ', 'ᴥ', 'ㅂ', 'ㅏ', 'ㄹ', 'ㄱ', 'ㅜ', 'ㄹ', 'ᴥ', 'ㅂ', 'ㅣ', 'ㅇ', 'ㅛ', 'ㅇ', 'ᴥ', 'ㅈ', 'ㅣ', 'ㅂ', 'ㅜ', 'ㄹ', 'ᴥ', 'ㄷ', 'ㅡ', 'ㅇ', 'ㅇ', 'ㅡ', 'ㄹ', 'ᴥ', 'ㅇ', 'ㅟ', 'ㅎ', 'ㅏ', 'ㄴ', 'ᴥ', 'ㄷ', 'ㅐ', 'ㅂ', 'ㅜ', 'ㄱ', 'ㅈ', 'ㅔ', 'ㅈ', 'ㅐ', 'ᴥ', 'ㅇ', 'ㅖ', 'ㅇ', 'ㅚ', 'ᴥ', 'ㅇ', 'ㅣ', 'ㄴ', 'ㅈ', 'ㅓ', 'ㅇ', 'ㅇ', 'ㅣ', 'ᴥ', 'ㅍ', 'ㅣ', 'ㄹ', 'ㅇ', 'ㅛ', 'ㅎ', 'ㅏ', 'ㄷ', 'ㅏ', '.']
PRED 8011: T@@ h@@ i@@ s i@@ s e@@ x@@ p@@ e@@ c@@ t@@ e@@ d t@@ h@@ e t@@ e@@ r@@ m@@ s s@@ h@@ i@@ n@@ g i@@ n t@@ h@@ e p@@ r@@ e@@ s@@ s r@@ e@@ l@@ f@@ .
PRED SCORE: -0.0777

[2020-12-11 16:09:01,742 INFO] 

# Detokenization

Even after the translation process is finished, it is still in a segment, so it is different from the actual sentence structure used by real people. Thus, when you perform a detoxification process, it is returned in the form of the actual sentence.

We Use "sed" for BPE Detokenization


In [18]:
!sed -i "s/@@ //g"  OpenNMT-py/Data/jamo2bpe/pred_50k.txt

# Post-processing

In [9]:
f = open('OpenNMT-py/Data/tgt-test.txt', 'r', encoding='utf-8')
txt = f.read()
txt[:1000]


# txt = txt.replace(' ', '')
# txt = txt.replace('ᴥ', ' ')

# with open("OpenNMT-py/Data/tgt-test-char1.txt", "w") as f:
#     f.write(txt)
    
# f = open('OpenNMT-py/Data/tgt-test-char1.txt', 'r', encoding='utf-8')
# txt = f.read()
# txt[:1000]  

'"According to descriptions by the police, Mr. Kim, who visited the PC-bang as a guest, had an argument with Mr. Shin while demanding that food left by other guests be cleared from his seat."\n"As Jamsil Girls\' High School (Principal Kim In-bong) is aiming to cultivate talents and good personality, the teachers and students are upgrading their career path programs through the ""Team-play of Trust""."\nFormer lawmaker Kim will lose both his right to vote and his right to run for 5 years if a fine of 1 million won or more is confirmed.\n"The working environment of Daejeon Industrial Park in Daedeok-gu, Daejeon will be improved."\n"Around 90t of reinforcement facilities were lost due to high waves at the Dongbang Breakwater Construction site in Wimi Port, Namwon-eup, Seogwipo-si, and a 100m median strip fell in the area of Nohyeong Rotary - Samsung Service Center in Jeju."\nIt is a program to make students value physical education and art.\n"The US Department of Justice prosecuted Assang

In [19]:
# f = open('OpenNMT-py/Data/jamo2morph/pred.txt', 'r', encoding='utf-8')
# txt = f.read()
# txt = txt.replace(' ', '')
# txt = txt.replace('ᴥ', ' ')

# with open("OpenNMT-py/Data/jamo2bpe/pred.txt", "w") as f:
#     f.write(txt)

f = open('OpenNMT-py/Data/jamo2bpe/pred_50k.txt', 'r', encoding='utf-8')
txt = f.read()
txt[:1000]  

'"Afterward, a former parents are disappearantly ther."\nTefension may is a vising may not politicies in the same po.\nThe largest resident KRW 8700 meeting beginest Mar.\nThe experience of the companies is cleased in Kim.\nThe place of the World so atcher than 100 cutcher.\nThe seconomy is what I want to show it is the beding seemont.\nBoth teams have been Parking first ballienged the matter.\n"The places are very 20,000 in but points and the recention."\nThe players of both may are shaking and lowere all change.\nThe first from place is to the first place is self.\nThe laways partients more should me different.\nIt is still for that I want to do it the professional day.\nThe ball for portunity is the first port.\nIt is also been a lot of poing the aintenside.\nAll second inversence was also a good in just once the next 1.\n"In the car words, 20 disered by team of the two compete."\nThe VS ure of the controversion and per asted in the guture.\nThere should be more to give big underss 

# Evaluation Using BLEU

Quantitative evaluation is performed on the sentence thus obtained. BLEU is a quantitative evaluation method for machine translation. You can see which model is superior by comparing it to the BLEU score you are comparing.

https://www.aclweb.org/anthology/P02-1040

In [20]:
!perl  OpenNMT-py/tools/multi-bleu.perl OpenNMT-py/Data/tgt-test.txt < OpenNMT-py/Data/jamo2bpe/pred_50k.txt

Use of uninitialized value in division (/) at OpenNMT-py/tools/multi-bleu.perl line 139, <STDIN> line 8014.
BLEU = 0.00, 16.8/1.2/0.0/0.0 (BP=0.168, ratio=0.360, hyp_len=81721, ref_len=227303)
